In [1]:
import os
import datetime
import warnings
import json
import polars as pl
import pandas as pd
import altair as alt

from src.najdi_rok import najdi_rok
from src.pocet_stran import pocet_stran
from src.bez_bordelu import bez_bordelu
from src.alt_friendly import alt_friendly
from src.hezke_jmeno import hezke_jmeno
from src.kristi_promin import kristi_promin
from src.zjisti_vazbu import zjisti_vazbu
from src.me_to_neurazi import me_to_neurazi

pl.Config(tbl_rows=100)
alt.data_transformers.disable_max_rows()
alt.themes.register('irozhlas', kristi_promin)
alt.themes.enable('irozhlas')
warnings.filterwarnings('ignore')

In [2]:
with open(os.path.join('src','kredity.json'), 'r', encoding='utf-8') as kredity:
    kredity = json.loads(kredity.read())

In [3]:
with open(os.path.join('barvy','barvy.json'), 'r', encoding='utf-8') as palety:
    palety = json.loads(palety.read())

In [4]:
df = pl.read_parquet('data/cnb_vyber.parquet')

In [5]:
df = df.with_columns(pl.col('008').map_elements(najdi_rok, return_dtype=int).alias('rok'))

In [6]:
petdvanula = pl.read_parquet("data/cnb_sloupce/520.parquet")
df = df.join(petdvanula, on='001', how='left')

In [7]:
tematicke_sloupce = ['072_x','245_a','245_c','245_p','246_a','500_a','520_a','520_b','521_a','648_a','650_a','650_x','650_z','650_y','651_a','653_a','655_a','964_a']

In [8]:
df = df.select(pl.col(['rok'] + tematicke_sloupce)).with_columns(pl.col(tematicke_sloupce).cast(pl.List(pl.String)).list.join(" "))
df = df.with_columns(pl.col(tematicke_sloupce).fill_null(' ')).with_columns(pl.concat_str([pl.col(t) for t in tematicke_sloupce], separator=" ").alias("keywords"))

In [9]:
def tema(label, keywords):
    return df.filter(pl.col('keywords').str.contains(keywords)).with_columns(téma = pl.lit(label)).with_columns(
               pl.col("rok").map_elements(
                   lambda x: datetime.date(year=x, month=1, day=1), 
                   return_dtype=pl.Date
               ).cast(pl.Datetime)
           )

In [10]:
warnings.filterwarnings("ignore")

In [11]:
def hledej_tema(label, keywords):
    return df.filter(pl.col('rok') > 1945).filter(pl.col('keywords').str.contains(keywords)).with_columns(téma = pl.lit(label)).with_columns(
               pl.col("rok").map_elements(
                   lambda x: datetime.date(year=x, month=1, day=1), 
                   return_dtype=pl.Date
               ).cast(pl.Datetime)
           )

In [12]:
def hledej_tema(label, keywords):
        return df.filter(pl.col('keywords').str.contains(keywords)).with_columns(téma = pl.lit(label))

In [13]:
predpo = df.filter(
    pl.col("rok").is_between(1987,1993)
).with_columns(
    pl.col("keywords").map_elements(lambda x: x.split(" "))
).explode("keywords")

In [14]:
predpo.filter(
    pl.col("rok").is_between(1987,1988)
).group_by('keywords').len().join(
    predpo.filter(
        pl.col("rok").is_between(1990,1992)
    ).group_by('keywords').len(), on='keywords', how='right'
).with_columns((pl.col('len_right') / pl.col('len')).alias('narust')).filter(pl.col('len_right') > 20).filter(pl.col('narust').is_null()).sort(by='len_right',descending=True).head(100)

shape: (100, 4)
┌──────┬────────────────┬───────────┬────────┐
│ len  ┆ keywords       ┆ len_right ┆ narust │
│ ---  ┆ ---            ┆ ---       ┆ ---    │
│ u32  ┆ str            ┆ u32       ┆ f64    │
╞══════╪════════════════╪═══════════╪════════╡
│ null ┆ sčítání        ┆ 3372      ┆ null   │
│ null ┆ bytů           ┆ 1289      ┆ null   │
│ null ┆ Sčítání        ┆ 721       ┆ null   │
│ null ┆ 1991.          ┆ 666       ┆ null   │
│ null ┆ domy,          ┆ 468       ┆ null   │
│ null ┆ Obyvatelstvo,  ┆ 467       ┆ null   │
│ null ┆ domácnosti.    ┆ 465       ┆ null   │
│ null ┆ střed.         ┆ 305       ┆ null   │
│ null ┆ ČSFR           ┆ 211       ┆ null   │
│ null ┆ demografická   ┆ 184       ┆ null   │
│ null ┆ obcí,          ┆ 100       ┆ null   │
│ null ┆ měst,          ┆ 94        ┆ null   │
│ null ┆ jednotky.      ┆ 94        ┆ null   │
│ null ┆ Souhrnné       ┆ 93        ┆ null   │
│ null ┆ 1990-1991      ┆ 82        ┆ null   │
│ null ┆ FoxPro         ┆ 81        ┆ null   │
│ null ┆ privatizace    ┆ 80        ┆ null   │
│ null ┆ daň            ┆ 77        ┆ null   │
│ null ┆ Norton         ┆ 69        ┆ null   │
│ null ┆ 1991-2000      ┆ 69        ┆ null   │
│ null ┆ horoskopy      ┆ 68        ┆ null   │
│ null ┆ alternativní   ┆ 62        ┆ null   │
│ null ┆ Daň            ┆ 60        ┆ null   │
│ null ┆ autobiografie  ┆ 59        ┆ null   │
│ null ┆ Patricia       ┆ 57        ┆ null   │
│ null ┆ Vandenbergová  ┆ 55        ┆ null   │
│ null ┆ magazíny       ┆ 55        ┆ null   │
│ null ┆ Quattro        ┆ 50        ┆ null   │
│ null ┆ Palackého,     ┆ 50        ┆ null   │
│ null ┆ (hledisko)     ┆ 50        ┆ null   │
│ null ┆ Grey           ┆ 50        ┆ null   │
│ null ┆ židovské       ┆ 48        ┆ null   │
│ null ┆ 0              ┆ 48        ┆ null   │
│ null ┆ zvěrokruhu)    ┆ 48        ┆ null   │
│ null ┆ Zane           ┆ 48        ┆ null   │
│ null ┆ (znamení       ┆ 48        ┆ null   │
│ null ┆ (semináře)     ┆ 47        ┆ null   │
│ null ┆ Garrigue       ┆ 47        ┆ null   │
│ null ┆ Západočeská    ┆ 45        ┆ null   │
│ null ┆ 1991-1992      ┆ 45        ┆ null   │
│ null ┆ Ježíš          ┆ 45        ┆ null   │
│ null ┆ 5.0            ┆ 44        ┆ null   │
│ null ┆ '90            ┆ 43        ┆ null   │
│ null ┆ 1990-1992      ┆ 43        ┆ null   │
│ null ┆ reforma        ┆ 43        ┆ null   │
│ null ┆ republika.     ┆ 42        ┆ null   │
│ null ┆ Poprvé         ┆ 42        ┆ null   │
│ null ┆ databázový     ┆ 42        ┆ null   │
│ null ┆ Federativní    ┆ 41        ┆ null   │
│ null ┆ Daně           ┆ 40        ┆ null   │
│ null ┆ [Přel.         ┆ 40        ┆ null   │
│ null ┆ podnikatelé    ┆ 40        ┆ null   │
│ null ┆ SRN            ┆ 40        ┆ null   │
│ null ┆ boží           ┆ 39        ┆ null   │
│ null ┆ erotické       ┆ 39        ┆ null   │
│ null ┆ Masaryk,       ┆ 39        ┆ null   │
│ null ┆ Okultismus     ┆ 38        ┆ null   │
│ null ┆ 90.,           ┆ 38        ┆ null   │
│ null ┆ Ježíše         ┆ 37        ┆ null   │
│ null ┆ Kancelářské    ┆ 37        ┆ null   │
│ null ┆ podnikatele    ┆ 37        ┆ null   │
│ null ┆ Novell         ┆ 37        ┆ null   │
│ null ┆ ES             ┆ 36        ┆ null   │
│ null ┆ 1948-1968      ┆ 36        ┆ null   │
│ null ┆ 1989-1990      ┆ 36        ┆ null   │
│ null ┆ Ezoterismus.   ┆ 36        ┆ null   │
│ null ┆ Škvorecký      ┆ 36        ┆ null   │
│ null ┆ SPEV           ┆ 35        ┆ null   │
│ null ┆ NetWare        ┆ 35        ┆ null   │
│ null ┆ řeholní        ┆ 35        ┆ null   │
│ null ┆ 1948-1989      ┆ 35        ┆ null   │
│ null ┆ přidané        ┆ 34        ┆ null   │
│ null ┆ Commander      ┆ 34        ┆ null   │
│ null ┆ obratu         ┆ 34        ┆ null   │
│ null ┆ parlamentní    ┆ 33        ┆ null   │
│ null ┆ [?]            ┆ 33        ┆ null   │
│ null ┆ sex            ┆ 32        ┆ null   │
│ null ┆ daňová         ┆ 32        ┆ null   │
│ null ┆ Panny          ┆ 32        ┆ null   │
│ null ┆ Windows        ┆ 32        

In [45]:
revoluce = {
    'povinnosti': '[Pp]ovinnost',
    'Ježíš': '[Jj]ežíš',
#    'volný čas': '[Vv]olný čas',
#    'přestavba': '[Pp]řestavb',
    'horoskopy': '[Hh]oroskop',
    'privatizace': '[Pr]ivatiza',
#    'kolektiv': '[Kk]olektiv',
#    'soukromník': '[Ss]oukrom(ý|ní)',
    'produktivita': '[Pp]roduktiv',
    'pionýr': ('[Pi]oný[rř]'),
    'skaut, junák': '([Ss]kaut|[Jj]uná[kc])',
    'spartakiáda': '[Ss]partakiá',
    'sokolský slet': '[Ss]okols\w{1,5}\sslet',
#    'solidarita': '[Ss]olid[áa]r',
#    'úspěchy': '[Úú]spě',
#    'demokracie': '[Dd]emokra',
#    'tyranie':'[Tt]yran',
    'RVHP': '(RVHP|Rada vzájemné hospodářské pomoci)',
    'ES/EU':'(Evropsk\w{1,3}\suni\w{1,4}|Evropsk\w{1,3}\sspolečen)'
    
#    'solidarita': '[Ss]olid[aá]',
#    'zisk': '[Zz]isk',
#    'tradice':'[Tt]radi[cč]',
#    'sex': '[S]ex',
    #'Marx': '[Mm]arx',
    #'Masaryk': '[Mm]asaryk',
}

titulek = "Vybraná témata knih ve 20. století"
podtitulek = "Co tečka, to kniha (včetně překladů a opakovaných vydání)"

finalni_graf_data = pl.concat([hledej_tema(tema, retezec) for tema, retezec in revoluce.items()]).filter(pl.col("rok").is_between(1901,1999)).with_columns(
                   pl.col("rok").map_elements(
                       lambda x: datetime.date(year=x, month=1, day=1), 
                       return_dtype=pl.Date
                   ).cast(pl.Datetime)
               )
finalni_graf_data

temata_zlomy = alt.Chart(
    finalni_graf_data.to_pandas(), title=alt.Title(titulek,subtitle=podtitulek)
).mark_circle(size=6, opacity=1).encode(
    x=alt.X("rok:T", title=None, axis=alt.Axis(domainOpacity=0, tickColor='#ECEDE6', tickCount=8)), 
    y=alt.Y('téma:N', 
            title=None, 
            axis=alt.Axis(domainOpacity=0, tickColor='white'),
            sort=[tema for tema, neco in revoluce.items()]), 
            yOffset=alt.YOffset("jitter:Q", scale=alt.Scale(range=[2, 15])), 
            color=alt.Color('téma:N', scale=alt.Scale(range=['#E09DA3']), 
            sort=[tema for tema, retezec in revoluce.items()]
).legend(None)
).transform_calculate(jitter="sqrt(-2*log(random()))*cos(2*PI*random())")

rulecolor = '#81A9D5'

rule1 = alt.Chart(alt.Data(values=[{'rok': '1948-02-25'}])).mark_rule(
    color=rulecolor,
    strokeDash=[1.5, 4]  # Optional: makes the line dashed
).encode(
    x='rok:T'
)

rule2 = alt.Chart(alt.Data(values=[{'rok': '1989-11-17'}])).mark_rule(
    color=rulecolor,
    strokeDash=[1.5, 4]  # Optional: makes the line dashed
).encode(
    x='rok:T'
)

# Add text annotation
text1 = alt.Chart(alt.Data(values=[{'rok': '1948-02-25', 'y': 0.3}])).mark_text(
    # angle=270,  # Rotates text vertically
    align='right',
    baseline='middle',
    dy=70,# Slight horizontal offset from the line
    dx=-6.5,
    text=['komunistický','převrat →'],
    font='Asap',
    size=8
).encode(
    x='rok:T',
    y=alt.value(0)  # Places text at bottom of chart
)


# Add text annotation
text2 = alt.Chart(alt.Data(values=[{'rok': '1989-11-17', 'y': 0.3}])).mark_text(
    # angle=270,  # Rotates text vertically
    align='right',
    baseline='middle',
    dy=73,# Slight horizontal offset from the line
    dx=-6.5,
    text=['sametová revoluce →'],
    font='Asap',
    size=8
).encode(
    x='rok:T',
    y=alt.value(0)  # Places text at bottom of chart
)

# Add text annotation
text3 = alt.Chart(alt.Data(values=[{'rok': '1918-10-28', 'y': 0.3}])).mark_text(
    # angle=270,  # Rotates text vertically
    align='right',
    baseline='middle',
    dy=70,# Slight horizontal offset from the line
    dx=-6.6,
    text=['založení','ČSR →'],
    font='Asap',
    size=8
).encode(
    x='rok:T',
    y=alt.value(0)  # Places text at bottom of chart
)

rule3 = alt.Chart(alt.Data(values=[{'rok': '1918-10-28'}])).mark_rule(
    color=rulecolor,
    strokeDash=[1.5, 4]  # Optional: makes the line dashed
).encode(
    x='rok:T'
)

temata_zlomy_komb = (temata_zlomy + rule1 + rule2 + rule3 + text1 + text2 + text3).properties(
    width=kredity['sirka'], autosize={'type': 'fit', 'contains': 'padding'}
).configure_view(stroke='transparent').configure_axisX(grid=False, domain=False)

temata_zlomy_komb

alt.LayerChart(...)

In [47]:
me_to_neurazi(temata_zlomy_komb, kredity=kredity['default'], soubor="01_temata")

<figure>
    <a href="https://data.irozhlas.cz/knihy-grafy/01_temata.svg" target="_blank">
    <img src="https://data.irozhlas.cz/knihy-grafy/01_temata.svg" width="100%" alt="Omlouváme se, ale alternativní text se nepodařilo vygenerovat. Texty v grafu by měly být čitelné ze zdrojového souboru SVG." />
    </a>
    </figure>
